# Скрипт для проверки соответствия репозитория сетевому диску

**Важная информация**, которую надо знать про этот скрипт

Коммиты осуществляются в репозитории, которые находятся в gitlab.ximc.ru. EduNet-content зеркалится на github.com И можно было бы парсить файлы с gitlab, но есть нюанс: он возвращает только первые 20 файлов из любой папки. Поэтому для проверки репозитория EduNet-content используется зеркало, и там все должно хорошо работать. А EduNet-web_dependencies парсится с gitlab.ximc.ru и выводит только первые 20 файлов, поэтому для части лекций может некорректно работать. Зеркалить его технически проблематично, поэтому единственный пока возможный выход — уменьшить количество заимствованных изображений до 20 штук.

Импортируем необходимые библиотеки

In [ ]:
from bs4 import BeautifulSoup
import requests

Вы будете работать и с gitlab.ximc.ru, и с github.com, поэтому Вам понадобятся два токена соответственно. Введите свои Github Access Token и Gitlab Access Token в ячейки ниже. Так как EduNet-web dependencies — приватный репозиторий, Вам нужен токен с доступом к приватному репозиторию на GitLab. Если Вы не знаете, что это и как его создать, смотрите [инструкцию по использованию скриптов](https://ximc.ru/projects/edunet/wiki/%D0%98%D0%BD%D1%81%D1%82%D1%80%D1%83%D0%BA%D1%86%D0%B8%D1%8F_%D0%BF%D0%BE_%D0%B8%D1%81%D0%BF%D0%BE%D0%BB%D1%8C%D0%B7%D0%BE%D0%B2%D0%B0%D0%BD%D0%B8%D1%8E_%D1%81%D0%BA%D1%80%D0%B8%D0%BF%D1%82%D0%BE%D0%B2/edit#%D0%9F%D1%80%D0%BE-Github-Access-Token-%D0%B8-GitLab-Access-Token).

In [ ]:
github_token = "Input Your GitHub Access Token Here"
gitlab_token = "Input Your GitLab Access Token Here"
dev_branch = "dev-2.0"

In [ ]:
gitlab_token = "Input Your GitLab Access Token Here"

Номера папок с лекциями, в которые надо "зайти":

In [ ]:
lectures = ["L01", "L02", "L03", "L04", "L05", "L06", "L07", "L08", "L09", "L10", "L11", "L12", "L13", "L14", "L15"]

Этот скрипт в EduNet-content проверяет только папку `out`. Для проверки исходников используйте скрипт **Compare_out_and_src.ipynb**.

Ячейка ниже — основная функция. Выполните её.

In [ ]:
def compare_host_and_repo(lecture):

    host_content = []
    host_wd = []
    repo_content = []
    repo_wd = []

    print(lecture, "\n")

    # СНАЧАЛА ПРОВЕРЯЕМ CONTENT

    #Парсим сетевой диск
    url_host_content = f'https://edunet.kea.su/repo/EduNet-content/{dev_branch}/{lecture}/out/'
    html_text = requests.get(url_host_content).text
    image_links = BeautifulSoup(html_text, 'lxml').find_all(href=True)[1:]
    for link in image_links:
        host_content.append(("".join([url_host_content, link.get('href')])).split("/")[-1])

    # Парсим репозиторий
    url_repo_content =f'https://api.github.com/repos/EPC-MSU/EduNet-content/contents/{dev_branch}/{lecture}/out/?ref=master'
    r = requests.get(url_repo_content, headers={'PRIVATE-TOKEN': gitlab_token})
    r.raise_for_status()
    data = r.json()
    repo_content = [x['name'] for x in data]

    print("EduNet-content \n")

    # Список файлов, которых не хватает в репозитории:
    diff_not_in_repo_content = list(set(host_content) - set(repo_content))
    if (len(diff_not_in_repo_content)>0):
        print("В репозитории не хватает:\n")
        for i in range(0, len(diff_not_in_repo_content)):
            print(diff_not_in_repo_content[i])

    # Список файлов, которые лишние в репозитории:
    diff_only_in_repo_content = list(set(repo_content) - set(host_content))
    if (len(diff_only_in_repo_content)>0):
        print("\nВ репозитории лишнее:\n")
        for i in range(0, len(diff_only_in_repo_content)):
            print(diff_only_in_repo_content[i])

    # ТУТ ПРОВЕРКА WEB_DEPENDENCIES

    #Парсим сетевой диск
    url_host_wd = f'https://edunet.kea.su/repo/EduNet-web_dependencies/{dev_branch}/{lecture}/'
    html_text = requests.get(url_host_wd).text
    image_links = BeautifulSoup(html_text, 'lxml').find_all(href=True)[1:]
    for link in image_links:
        host_wd.append(("".join([url_host_content, link.get('href')])).split("/")[-1])

    # Парсим репозиторий
    url_repo_wd =f'https://gitlab.ximc.ru/api/v4/projects/87/repository/tree/?path={dev_branch}/{lecture}&private_token={gitlab_token}'
    r = requests.get(url_repo_wd)
    data = r.json()
    repo_wd = [x['name'] for x in data]

    print("\nEduNet-web_dependencies \n")

    # Список файлов, которых не хватает в репозитории:
    diff_not_in_repo_wd = list(set(host_wd) - set(repo_wd))
    if (len(diff_not_in_repo_wd)>0):
        print("В репозитории не хватает:\n")
        for i in range(0, len(diff_not_in_repo_wd)):
            print(diff_not_in_repo_wd[i])

    # Список файлов, которые лишние в репозитории:
    diff_only_in_repo_wd = list(set(repo_wd) - set(host_wd))
    if (len(diff_only_in_repo_wd)>0):
        print("\nВ репозитории лишнее:\n")
        for i in range(0, len(diff_only_in_repo_wd)):
            print(diff_only_in_repo_wd[i])

А здесь задайте переменной `lecture_num` номер проверяемой лекции и получите по ней всю информацию.

In [ ]:
lecture_num = 1
compare_host_and_repo(lectures[lecture_num-1])